# Curacao Risk Level for Extreme Sea Level Hazard Using Gornitz et al. (1994)
# Curacao Multi-Criteria Risk Level for Extreme Sea Level Hazard Using Mclaughlin and Cooper (2010)


In [1]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
from shapely.geometry import Point, Polygon
from scipy.spatial import KDTree
import numpy as np

# Additional imports
import pystac_client
import xarray as xr
import pathlib
import os
import geopandas as gpd
import matplotlib as mpl
from matplotlib import colors
import rasterio

import cartopy.crs as ccrs
import cartopy
import plotly.graph_objects as go
import plotly.express as px
from rasterio.plot import show

import matplotlib.colors as mcolors
from shapely.geometry import Point
import pandas as pd

from tqdm import tqdm

import webbrowser
from pathlib import Path
import os
import time

from itertools import compress
import pandas as pd

import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio

from tqdm import tqdm

from shapely.geometry import box



In [2]:
Exposure_df_kmeans=pd.read_csv(r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Caribbean Thesis_Results\Exposure\Caribbean_Exposure_classified_kmeans.csv")
# Exposure_df["Sediment_Type - Exposure level"]=Exposure_df["Sediment Type"]


Exposure_df_kmeans

transect_id country_id      continent        country_name  \
0       BOX_116_353_2        COL  South America            Colombia   
1       BOX_116_353_3        COL  South America            Colombia   
2       BOX_116_353_4        COL  South America            Colombia   
3       BOX_116_353_5        COL  South America            Colombia   
4       BOX_116_353_6        COL  South America            Colombia   
...               ...        ...            ...                 ...   
37504  BOX_139_002_61        DOM  North America  Dominican Republic   
37505  BOX_139_002_62        DOM  North America  Dominican Republic   
37506  BOX_139_002_63        DOM  North America  Dominican Republic   
37507  BOX_139_002_64        DOM  North America  Dominican Republic   
37508  BOX_139_002_65        DOM  North America  Dominican Republic   

       Percentage of Built Up Area_kmeans  \
0                                     0.0   
1                                     0.0   
2                                     0.0   
3                                     0.0   
4                                     0.0   
...                                   ...   
37504                                 0.0   
37505                                 0.0   
37506                                 0.0   
37507                                 0.0   
37508                                 0.0   

       LECZ Area÷LECZ mean elevation_kmeans  \
0                              1.366501e+06   
1                              1.974146e+06   
2                              3.834474e+06   
3                              5.239073e+06   
4                              6.112962e+06   
...                                     ...   
37504                          1.793014e+06   
37505                          1.861771e+06   
37506                          1.970466e+06   
37507                          2.126400e+06   
37508                          2.078267e+06   

       Neashore Slope (tanβ or m^-1)_kmeans  \
0                                 11.291917   
1                                 13.060951   
2                                 13.060951   
3                                 11.420912   
4                                 11.420912   
...                                     ...   
37504                              3.867398   
37505                              3.867398   
37506                              3.790441   
37507                              3.790441   
37508                              4.570359   

       Population Within 1km of the coastline_kmeans  Sediment Type_kmeans  \
0                                                0.0                   4.0   
1                                                0.0                   2.0   
2                                                0.0                   4.0   
3                                                0.0                   2.0   
4                                                0.0                   2.0   
...                                              ...                   ...   
37504                                         1593.0                   4.0   
37505                                         2227.0                   4.0   
37506                                         2710.0                   4.0   
37507                                         2617.0                   4.0   
37508                                         1775.0                   4.0   

                                        geometry  \
0            POINT (-71.8798045985 12.250683718)   
1        POINT (-71.87698143850001 12.247308305)   
2           POINT (-71.8756318462 12.2431443263)   
3           POINT (-71.8752334021 12.2387721729)   
4           POINT (-71.8748349513 12.2343999454)   
...                                          ...   
37504       POINT (-71.6681862112 17.9652589019)   
37505       POINT (-71.6662284163 17.9614175026)   
37506        POINT (-71.664582619 17.9574419454)   
37507  POINT (-71.6629367897 

# Add the kmeans for built up percentage, Nearshore slope and population

In [3]:
Exposure_df=pd.read_csv(r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Caribbean Thesis_Results\Exposure\Caribbean_Exposure_classified_percentile.csv")
# Exposure_df["Sediment_Type - Exposure level"]=Exposure_df["Sediment Type"]




Exposure_df.iloc[:,10]=Exposure_df_kmeans.iloc[:,10] #built up %
Exposure_df.iloc[:,13]=Exposure_df_kmeans.iloc[:,13] #pop
Exposure_df.iloc[:,12]=Exposure_df_kmeans.iloc[:,12] #ns
Exposure_df

transect_id country_id      continent        country_name  \
0       BOX_116_353_2        COL  South America            Colombia   
1       BOX_116_353_3        COL  South America            Colombia   
2       BOX_116_353_4        COL  South America            Colombia   
3       BOX_116_353_5        COL  South America            Colombia   
4       BOX_116_353_6        COL  South America            Colombia   
...               ...        ...            ...                 ...   
37504  BOX_139_002_61        DOM  North America  Dominican Republic   
37505  BOX_139_002_62        DOM  North America  Dominican Republic   
37506  BOX_139_002_63        DOM  North America  Dominican Republic   
37507  BOX_139_002_64        DOM  North America  Dominican Republic   
37508  BOX_139_002_65        DOM  North America  Dominican Republic   

       Percentage of Built Up Area_percentile  \
0                                         0.0   
1                                         0.0   
2                                         0.0   
3                                         0.0   
4                                         0.0   
...                                       ...   
37504                                     0.0   
37505                                     0.0   
37506                                     0.0   
37507                                     0.0   
37508                                     0.0   

       LECZ Area÷LECZ mean elevation_percentile  \
0                                  1.366501e+06   
1                                  1.974146e+06   
2                                  3.834474e+06   
3                                  5.239073e+06   
4                                  6.112962e+06   
...                                         ...   
37504                              1.793014e+06   
37505                              1.861771e+06   
37506                              1.970466e+06   
37507                              2.126400e+06   
37508                              2.078267e+06   

       Neashore Slope (tanβ or m^-1)_percentile  \
0                                     11.291917   
1                                     13.060951   
2                                     13.060951   
3                                     11.420912   
4                                     11.420912   
...                                         ...   
37504                                  3.867398   
37505                                  3.867398   
37506                                  3.790441   
37507                                  3.790441   
37508                                  4.570359   

       Population Within 1km of the coastline_percentile  \
0                                                    0.0   
1                                                    0.0   
2                                                    0.0   
3                                                    0.0   
4                                                    0.0   
...                                                  ...   
37504                                             1593.0   
37505                                             2227.0   
37506                                             2710.0   
37507                                             2617.0   
37508                                             1775.0   

       Sediment Type_percentile                                   geometry  \
0                           4.0        POINT (-71.8798045985 12.250683718)   
1                           2.0    POINT (-71.87698143850001 12.247308305)   
2                           4.0       POINT (-71.8756318462 12.2431443263)   
3                           2.0       POINT (-71.8752334021 12.2387721729)   
4                           2.0       POINT (-71.8748349513 12.2343999454)   
...                         ...                                        ...   
37504                       4.0       POINT (-71.6681862112 17.9652589019) 

In [4]:
# Vulnerability_df=pd.read_csv(r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Caribbean Thesis_Results\Vulnerability\Caribbean_Vulnerability_classified_percentile.csv")

# Vulnerability_df

In [5]:
Hazard_df=pd.read_csv(r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Caribbean Thesis_Results\Hazard\Caribbean_Hazard_classified_percentile.csv")
Hazard_df

transect_id country_id      continent        country_name  \
0       BOX_116_353_2        COL  South America            Colombia   
1       BOX_116_353_3        COL  South America            Colombia   
2       BOX_116_353_4        COL  South America            Colombia   
3       BOX_116_353_5        COL  South America            Colombia   
4       BOX_116_353_6        COL  South America            Colombia   
...               ...        ...            ...                 ...   
37504  BOX_139_002_61        DOM  North America  Dominican Republic   
37505  BOX_139_002_62        DOM  North America  Dominican Republic   
37506  BOX_139_002_63        DOM  North America  Dominican Republic   
37507  BOX_139_002_64        DOM  North America  Dominican Republic   
37508  BOX_139_002_65        DOM  North America  Dominican Republic   

       ESL_100yrRP_percentile  EWH_100yrRP_percentile  \
0                    0.946771                4.455543   
1                    0.946771                4.455543   
2                    0.946771                4.455543   
3                    0.946771                4.455543   
4                    0.946771                4.455543   
...                       ...                     ...   
37504                1.246410                6.922152   
37505                1.246410                6.922152   
37506                1.246410                6.922152   
37507                1.246410                6.922152   
37508                1.246410                6.922152   

       Land_Subsidence_2010_percentile  Shoreline_Change_Rate_PC_percentile  \
0                                  NaN                           -16.441771   
1                                  NaN                             0.335379   
2                                  NaN                             1.878836   
3                                  NaN                             0.490707   
4                                  NaN                            -0.052123   
...                                ...                                  ...   
37504                              2.0                             0.288753   
37505                              2.0                             0.166001   
37506                              2.0                             0.092415   
37507                              2.0                            -0.027472   
37508                              2.0                            -0.094827   

       Cat3_Hurricane_Return_Period_PC_percentile  \
0                                        7.042254   
1                                        7.042254   
2                                        7.042254   
3                                        7.042254   
4                                        7.042254   
...                                           ...   
37504                                    6.369427   
37505                                    6.369427   
37506                                    6.369427   
37507                                    6.369427   
37508                                    6.369427   

                                        geometry  \
0            POINT (-71.8798045985 12.250683718)   
1        POINT (-71.87698143850001 12.247308305)   
2           POINT (-71.8756318462 12.2431443263)   
3           POINT (-71.8752334021 12.2387721729)   
4           POINT (-71.8748349513 12.2343999454)   
...                                          ...   
37504       POINT (-71.6681862112 17.9652589019)   
37505       POINT (-71.6662284163 17.9614175026)   
37506        POINT (-71.664582619 17.9574419454)   
37507  POINT (-71.6629367897 17.953466310899998)   
37508  POINT (-71.6612909283 17.949490598900002)   

       ESL_100yrRP_percentile - Hazard level  \
0                                        1.0   
1                                        1.0   
2                                        1.0   
3                                        1.0   
4                    

Addititive Combination

In [6]:
save_directory=r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Caribbean Thesis_Results\Combination\Risk_Level_PC_multi-haz_H-E"
img_directory_path=r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Caribbean Thesis_Results\Combination\Risk_Level_PC_multi-haz_H-E\Plots"
os.makedirs(save_directory, exist_ok=True)
os.makedirs(img_directory_path, exist_ok=True)

Discrete_Risk_Bins= True
Both_Plots=True

In [7]:
Hazard_df["multi-haz additive H-E CVI"]=(np.nansum(Hazard_df.iloc[:,-5:],axis=1)/len(Hazard_df.iloc[0,-5:]))
Hazard_df

transect_id country_id      continent        country_name  \
0       BOX_116_353_2        COL  South America            Colombia   
1       BOX_116_353_3        COL  South America            Colombia   
2       BOX_116_353_4        COL  South America            Colombia   
3       BOX_116_353_5        COL  South America            Colombia   
4       BOX_116_353_6        COL  South America            Colombia   
...               ...        ...            ...                 ...   
37504  BOX_139_002_61        DOM  North America  Dominican Republic   
37505  BOX_139_002_62        DOM  North America  Dominican Republic   
37506  BOX_139_002_63        DOM  North America  Dominican Republic   
37507  BOX_139_002_64        DOM  North America  Dominican Republic   
37508  BOX_139_002_65        DOM  North America  Dominican Republic   

       ESL_100yrRP_percentile  EWH_100yrRP_percentile  \
0                    0.946771                4.455543   
1                    0.946771                4.455543   
2                    0.946771                4.455543   
3                    0.946771                4.455543   
4                    0.946771                4.455543   
...                       ...                     ...   
37504                1.246410                6.922152   
37505                1.246410                6.922152   
37506                1.246410                6.922152   
37507                1.246410                6.922152   
37508                1.246410                6.922152   

       Land_Subsidence_2010_percentile  Shoreline_Change_Rate_PC_percentile  \
0                                  NaN                           -16.441771   
1                                  NaN                             0.335379   
2                                  NaN                             1.878836   
3                                  NaN                             0.490707   
4                                  NaN                            -0.052123   
...                                ...                                  ...   
37504                              2.0                             0.288753   
37505                              2.0                             0.166001   
37506                              2.0                             0.092415   
37507                              2.0                            -0.027472   
37508                              2.0                            -0.094827   

       Cat3_Hurricane_Return_Period_PC_percentile  \
0                                        7.042254   
1                                        7.042254   
2                                        7.042254   
3                                        7.042254   
4                                        7.042254   
...                                           ...   
37504                                    6.369427   
37505                                    6.369427   
37506                                    6.369427   
37507                                    6.369427   
37508                                    6.369427   

                                        geometry  \
0            POINT (-71.8798045985 12.250683718)   
1        POINT (-71.87698143850001 12.247308305)   
2           POINT (-71.8756318462 12.2431443263)   
3           POINT (-71.8752334021 12.2387721729)   
4           POINT (-71.8748349513 12.2343999454)   
...                                          ...   
37504       POINT (-71.6681862112 17.9652589019)   
37505       POINT (-71.6662284163 17.9614175026)   
37506        POINT (-71.664582619 17.9574419454)   
37507  POINT (-71.6629367897 17.953466310899998)   
37508  POINT (-71.6612909283 17.949490598900002)   

       ESL_100yrRP_percentile - Hazard level  \
0                                        1.0   
1                                        1.0   
2                                        1.0   
3                                        1.0   
4                    

In [8]:
# UNCOMMENT AS NEEDED

gornitz_hazard_used=Hazard_df.columns[-1]  #Toggle as needed between -5 and -1



Value_to_show=title_name=gornitz_hazard_used.replace(" - Hazard level","")


title_name=gornitz_hazard_used.replace(" - Hazard level","")

gornitz_ESL=pd.concat([Hazard_df.iloc[:,0],Hazard_df[gornitz_hazard_used],Exposure_df.iloc[:,-5:]],axis=1)
gornitz_ESL

transect_id  multi-haz additive H-E CVI  \
0       BOX_116_353_2                         2.0   
1       BOX_116_353_3                         1.2   
2       BOX_116_353_4                         1.2   
3       BOX_116_353_5                         1.2   
4       BOX_116_353_6                         1.2   
...               ...                         ...   
37504  BOX_139_002_61                         2.0   
37505  BOX_139_002_62                         2.0   
37506  BOX_139_002_63                         2.0   
37507  BOX_139_002_64                         2.0   
37508  BOX_139_002_65                         2.0   

       Percentage of Built Up Area_percentile - Exposure level_percentile  \
0                                                      1                    
1                                                      1                    
2                                                      1                    
3                                                      1                    
4                                                      1                    
...                                                  ...                    
37504                                                  1                    
37505                                                  1                    
37506                                                  1                    
37507                                                  1                    
37508                                                  1                    

       LECZ Area÷LECZ mean elevation_percentile - Exposure level_percentile  \
0                                                      4                      
1                                                      5                      
2                                                      5                      
3                                                      5                      
4                                                      5                      
...                                                  ...                      
37504                                                  4                      
37505                                                  4                      
37506                                                  5                      
37507                                                  5                      
37508                                                  5                      

       Neashore Slope (tanβ or m^-1)_percentile - Exposure level_percentile  \
0                                                    4.0                      
1                                                    4.0                      
2                                                    4.0                      
3                                                    4.0                      
4                                                    4.0                      
...                                                  ...                      
37504                                                3.0                      
37505                                                3.0                      
37506                                                3.0                      
37507                                                3.0                      
37508                                                3.0                      

       Population Within 1km of the coastline_percentile - Exposure level_percentile  \
0                                                      1                               
1                                                      1                               
2                                                      1                               
3                                                      1                               
4                                                      1                               
...                   

In [9]:
# Define Hazard units to show on plot

if "ESL" in gornitz_hazard_used:
    units="m"
if "EWH" in gornitz_hazard_used:
    units="m"
if "Change_rate" in gornitz_hazard_used:
    units="m/yr"
if "Land" in gornitz_hazard_used:
    units=""
if "Cat3" in gornitz_hazard_used:
    units="years"
if "multi" in gornitz_hazard_used:
    units=""

Haz_Component= Hazard_df[Value_to_show].apply(lambda x: f"{Value_to_show} {x:.2f}{units}")

In [10]:
indicator_num=len(gornitz_ESL.columns)-1
indicator_num

6

In [11]:
if indicator_num>6:
    var=" (Haz_Exp_Vul)"
else:
    var=" (Haz_Exp)"

In [12]:
gornitz_ESL_filled=gornitz_ESL.copy()
gornitz_ESL_filled["Risk Level"]=(gornitz_ESL[gornitz_hazard_used]+(np.nansum(gornitz_ESL.iloc[:,2:7],axis=1)/len(gornitz_ESL.iloc[0,2:7])))/2
# gornitz_ESL_filled["Risk Level Class"] = np.round(gornitz_ESL_filled["Risk Level"])
gornitz_ESL_filled["Risk Level Class"] = np.nan
gornitz_ESL_filled
# 1.000240	

transect_id  multi-haz additive H-E CVI  \
0       BOX_116_353_2                         2.0   
1       BOX_116_353_3                         1.2   
2       BOX_116_353_4                         1.2   
3       BOX_116_353_5                         1.2   
4       BOX_116_353_6                         1.2   
...               ...                         ...   
37504  BOX_139_002_61                         2.0   
37505  BOX_139_002_62                         2.0   
37506  BOX_139_002_63                         2.0   
37507  BOX_139_002_64                         2.0   
37508  BOX_139_002_65                         2.0   

       Percentage of Built Up Area_percentile - Exposure level_percentile  \
0                                                      1                    
1                                                      1                    
2                                                      1                    
3                                                      1                    
4                                                      1                    
...                                                  ...                    
37504                                                  1                    
37505                                                  1                    
37506                                                  1                    
37507                                                  1                    
37508                                                  1                    

       LECZ Area÷LECZ mean elevation_percentile - Exposure level_percentile  \
0                                                      4                      
1                                                      5                      
2                                                      5                      
3                                                      5                      
4                                                      5                      
...                                                  ...                      
37504                                                  4                      
37505                                                  4                      
37506                                                  5                      
37507                                                  5                      
37508                                                  5                      

       Neashore Slope (tanβ or m^-1)_percentile - Exposure level_percentile  \
0                                                    4.0                      
1                                                    4.0                      
2                                                    4.0                      
3                                                    4.0                      
4                                                    4.0                      
...                                                  ...                      
37504                                                3.0                      
37505                                                3.0                      
37506                                                3.0                      
37507                                                3.0                      
37508                                                3.0                      

       Population Within 1km of the coastline_percentile - Exposure level_percentile  \
0                                                      1                               
1                                                      1                               
2                                                      1                               
3                                                      1                               
4                                                      1                               
...                   

In [13]:
#Classifying  Risk levels based in 20%, 40%, 60%, and 80& percentiles


RL1 = np.percentile(gornitz_ESL_filled["Risk Level"].dropna(), 20)
RL2 = np.percentile(gornitz_ESL_filled["Risk Level"].dropna(), 40)
RL3 = np.percentile(gornitz_ESL_filled["Risk Level"].dropna(), 60)
RL4 = np.percentile(gornitz_ESL_filled["Risk Level"].dropna(), 80)


gornitz_ESL_filled.loc[gornitz_ESL_filled["Risk Level"] <= RL1, "Risk Level Class"] = 1
gornitz_ESL_filled.loc[(gornitz_ESL_filled["Risk Level"] > RL1) & (gornitz_ESL_filled["Risk Level"] <= RL2), "Risk Level Class"] = 2
gornitz_ESL_filled.loc[(gornitz_ESL_filled["Risk Level"] > RL2) & (gornitz_ESL_filled["Risk Level"] <= RL3), "Risk Level Class"] = 3
gornitz_ESL_filled.loc[(gornitz_ESL_filled["Risk Level"] > RL3) & (gornitz_ESL_filled["Risk Level"] <= RL4), "Risk Level Class"] = 4
gornitz_ESL_filled.loc[gornitz_ESL_filled["Risk Level"] > RL4, "Risk Level Class"] = 5

gornitz_ESL_filled

transect_id  multi-haz additive H-E CVI  \
0       BOX_116_353_2                         2.0   
1       BOX_116_353_3                         1.2   
2       BOX_116_353_4                         1.2   
3       BOX_116_353_5                         1.2   
4       BOX_116_353_6                         1.2   
...               ...                         ...   
37504  BOX_139_002_61                         2.0   
37505  BOX_139_002_62                         2.0   
37506  BOX_139_002_63                         2.0   
37507  BOX_139_002_64                         2.0   
37508  BOX_139_002_65                         2.0   

       Percentage of Built Up Area_percentile - Exposure level_percentile  \
0                                                      1                    
1                                                      1                    
2                                                      1                    
3                                                      1                    
4                                                      1                    
...                                                  ...                    
37504                                                  1                    
37505                                                  1                    
37506                                                  1                    
37507                                                  1                    
37508                                                  1                    

       LECZ Area÷LECZ mean elevation_percentile - Exposure level_percentile  \
0                                                      4                      
1                                                      5                      
2                                                      5                      
3                                                      5                      
4                                                      5                      
...                                                  ...                      
37504                                                  4                      
37505                                                  4                      
37506                                                  5                      
37507                                                  5                      
37508                                                  5                      

       Neashore Slope (tanβ or m^-1)_percentile - Exposure level_percentile  \
0                                                    4.0                      
1                                                    4.0                      
2                                                    4.0                      
3                                                    4.0                      
4                                                    4.0                      
...                                                  ...                      
37504                                                3.0                      
37505                                                3.0                      
37506                                                3.0                      
37507                                                3.0                      
37508                                                3.0                      

       Population Within 1km of the coastline_percentile - Exposure level_percentile  \
0                                                      1                               
1                                                      1                               
2                                                      1                               
3                                                      1                               
4                                                      1                               
...                   

In [14]:


df = gornitz_ESL.iloc[:,1:]

# Identify columns with NaN values
nan_columns = df.columns[df.isna().any()].tolist()

# Create a new column 'NaN_Columns' containing list of column names with NaN values for each row
gornitz_ESL_filled['Uncertainty_Columns'] = df.apply(lambda row: [col for col in nan_columns if pd.isna(row[col])], axis=1)
gornitz_ESL_filled['Uncertainty_Columns_length'] = gornitz_ESL_filled['Uncertainty_Columns'].apply(len)

df


multi-haz additive H-E CVI  \
0                             2.0   
1                             1.2   
2                             1.2   
3                             1.2   
4                             1.2   
...                           ...   
37504                         2.0   
37505                         2.0   
37506                         2.0   
37507                         2.0   
37508                         2.0   

       Percentage of Built Up Area_percentile - Exposure level_percentile  \
0                                                      1                    
1                                                      1                    
2                                                      1                    
3                                                      1                    
4                                                      1                    
...                                                  ...                    
37504                                                  1                    
37505                                                  1                    
37506                                                  1                    
37507                                                  1                    
37508                                                  1                    

       LECZ Area÷LECZ mean elevation_percentile - Exposure level_percentile  \
0                                                      4                      
1                                                      5                      
2                                                      5                      
3                                                      5                      
4                                                      5                      
...                                                  ...                      
37504                                                  4                      
37505                                                  4                      
37506                                                  5                      
37507                                                  5                      
37508                                                  5                      

       Neashore Slope (tanβ or m^-1)_percentile - Exposure level_percentile  \
0                                                    4.0                      
1                                                    4.0                      
2                                                    4.0                      
3                                                    4.0                      
4                                                    4.0                      
...                                                  ...                      
37504                                                3.0                      
37505                                                3.0                      
37506                                                3.0                      
37507                                                3.0                      
37508                                                3.0                      

       Population Within 1km of the coastline_percentile - Exposure level_percentile  \
0                                                      1                               
1                                                      1                               
2                                                      1                               
3                                                      1                               
4                                                      1                               
...                                                  ...                               
37504                                                  2                               
37505                              

In [15]:

gornitz_ESL_filled["Confindence %"]=100*(indicator_num-gornitz_ESL_filled['Uncertainty_Columns'].apply(len))/indicator_num
gornitz_ESL_filled

transect_id  multi-haz additive H-E CVI  \
0       BOX_116_353_2                         2.0   
1       BOX_116_353_3                         1.2   
2       BOX_116_353_4                         1.2   
3       BOX_116_353_5                         1.2   
4       BOX_116_353_6                         1.2   
...               ...                         ...   
37504  BOX_139_002_61                         2.0   
37505  BOX_139_002_62                         2.0   
37506  BOX_139_002_63                         2.0   
37507  BOX_139_002_64                         2.0   
37508  BOX_139_002_65                         2.0   

       Percentage of Built Up Area_percentile - Exposure level_percentile  \
0                                                      1                    
1                                                      1                    
2                                                      1                    
3                                                      1                    
4                                                      1                    
...                                                  ...                    
37504                                                  1                    
37505                                                  1                    
37506                                                  1                    
37507                                                  1                    
37508                                                  1                    

       LECZ Area÷LECZ mean elevation_percentile - Exposure level_percentile  \
0                                                      4                      
1                                                      5                      
2                                                      5                      
3                                                      5                      
4                                                      5                      
...                                                  ...                      
37504                                                  4                      
37505                                                  4                      
37506                                                  5                      
37507                                                  5                      
37508                                                  5                      

       Neashore Slope (tanβ or m^-1)_percentile - Exposure level_percentile  \
0                                                    4.0                      
1                                                    4.0                      
2                                                    4.0                      
3                                                    4.0                      
4                                                    4.0                      
...                                                  ...                      
37504                                                3.0                      
37505                                                3.0                      
37506                                                3.0                      
37507                                                3.0                      
37508                                                3.0                      

       Population Within 1km of the coastline_percentile - Exposure level_percentile  \
0                                                      1                               
1                                                      1                               
2                                                      1                               
3                                                      1                               
4                                                      1                               
...                   

In [16]:
# Read the CSV file into a DataFrame
circle_center_df = Exposure_df


# Identify the correct geometry column (replace 'geometry_column_name' with the actual column name)
geometry_column_name = 'geometry'
circle_center_df['x'] = circle_center_df[geometry_column_name].apply(lambda point_str: float(point_str.strip('POINT ()').split()[0]))
circle_center_df['y'] = circle_center_df[geometry_column_name].apply(lambda point_str: float(point_str.strip('POINT ()').split()[1]))

circle_center_df = circle_center_df.drop(columns=[geometry_column_name])

# Create the GeoDataFrame with the correct geometry column
gornitz_ESL_filled_gdf = gpd.GeoDataFrame(gornitz_ESL_filled, geometry=gpd.points_from_xy(circle_center_df.x, circle_center_df.y))



gornitz_ESL_filled_gdf

transect_id  multi-haz additive H-E CVI  \
0       BOX_116_353_2                         2.0   
1       BOX_116_353_3                         1.2   
2       BOX_116_353_4                         1.2   
3       BOX_116_353_5                         1.2   
4       BOX_116_353_6                         1.2   
...               ...                         ...   
37504  BOX_139_002_61                         2.0   
37505  BOX_139_002_62                         2.0   
37506  BOX_139_002_63                         2.0   
37507  BOX_139_002_64                         2.0   
37508  BOX_139_002_65                         2.0   

       Percentage of Built Up Area_percentile - Exposure level_percentile  \
0                                                      1                    
1                                                      1                    
2                                                      1                    
3                                                      1                    
4                                                      1                    
...                                                  ...                    
37504                                                  1                    
37505                                                  1                    
37506                                                  1                    
37507                                                  1                    
37508                                                  1                    

       LECZ Area÷LECZ mean elevation_percentile - Exposure level_percentile  \
0                                                      4                      
1                                                      5                      
2                                                      5                      
3                                                      5                      
4                                                      5                      
...                                                  ...                      
37504                                                  4                      
37505                                                  4                      
37506                                                  5                      
37507                                                  5                      
37508                                                  5                      

       Neashore Slope (tanβ or m^-1)_percentile - Exposure level_percentile  \
0                                                    4.0                      
1                                                    4.0                      
2                                                    4.0                      
3                                                    4.0                      
4                                                    4.0                      
...                                                  ...                      
37504                                                3.0                      
37505                                                3.0                      
37506                                                3.0                      
37507                                                3.0                      
37508                                                3.0                      

       Population Within 1km of the coastline_percentile - Exposure level_percentile  \
0                                                      1                               
1                                                      1                               
2                                                      1                               
3                                                      1                               
4                                                      1                               
...                   

In [17]:
# import os
# from dotenv import load_dotenv

# # Load the .env file
# load_dotenv(r'C:\Users\rowe\Documents\GitHub\coclicodata\.env')

# # Access the Mapbox Access Token
# mapbox_access_token = os.getenv('MAPBOX_ACCESS_TOKEN')

# print("Mapbox Access Token:", mapbox_access_token)

In [18]:
img_lat = 18.1
img_lon = -77.3
view_width = 10

In [19]:
if Discrete_Risk_Bins:

    long_name="Risk Level Class"
    # color_scale = ['#33f510','#3CB371','#FFFF00', '#FFA500','#FF4500']
    label_dict = {
    1: "Very Low",
    2: "Low",
    3: "Medium",
    4: "High",
    5: "Very High"}

    colors = {'Very Low': '#33f510', 'Low': '#3CB371', 'Medium': '#FFFF00', 'High': '#FFA500', 'Very High': '#FF4500'}

    gornitz_ESL_filled_gdf[Value_to_show] = Haz_Component

    #Sorted for Risk level view
    sorted_CCN=gornitz_ESL_filled_gdf.sort_values(long_name)


    # Create scatter map plot
    fig_region = px.scatter_mapbox(sorted_CCN,
                            lat=sorted_CCN["geometry"].y,
                            lon=sorted_CCN["geometry"].x,
                            # hover_name=sorted_CCN[long_name].replace(label_dict),
                            hover_name=Value_to_show,
                            color=sorted_CCN[long_name].replace(label_dict),
                            # color=sorted_CCN[long_name],
                            color_discrete_map=colors,
                            mapbox_style="carto-positron",width=2000,
                            height=1200)


    # Update map layout to adjust center and zoom
    fig_region.update_layout(mapbox=dict(center=dict(lat=img_lat + 1, lon=img_lon + 4), zoom=5.5),
                    title=f"{gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk')}{var} Discrete Distribution along Caribbean's shoreline")

    fig_region .update_layout(legend=dict(
    traceorder='normal',
    title=long_name,
    title_font=dict(size=16),
    itemsizing='constant',))
    fig_region.show()


    fig_name_shoreline=gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk') +var+"Discrete- Caribbean.png"
    pio.write_image(fig_region, os.path.join(img_directory_path, fig_name_shoreline))

In [20]:

if not Discrete_Risk_Bins or Both_Plots:

    long_name = "Risk Level"

    print_val=gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk') 
    # Define tick names

    lat = 18.1
    lon = -77.3
    view_width = 10
    # Define tick names
    tick_names = ["Very Low", "Low", "Moderate", "High", "Very High"]

    tk1=np.min(gornitz_ESL_filled_gdf[long_name].dropna())
    tk5=np.max(gornitz_ESL_filled_gdf[long_name].dropna())
    tk3=np.mean([tk1,tk5])
    tk4=np.mean([tk3,tk5])
    tk2=np.mean([tk3,tk1])



    
    tick_vals= [tk1, tk2,tk3, tk4, tk5]
   

    # Define parameters

    color_scale = ['#33f510', '#3CB371', '#FFFF00', '#FFA500', '#FF4500']

    # Update Hazard Component values
    gornitz_ESL_filled_gdf[Value_to_show] = Haz_Component

    # Sort values for Risk level view
    sorted_CCN = gornitz_ESL_filled_gdf.sort_values(long_name)

    # Create scatter map plot
    fig_region = px.scatter_mapbox(sorted_CCN,
                                    lat=sorted_CCN["geometry"].y,
                                    lon=sorted_CCN["geometry"].x,
                                    hover_name=Value_to_show,
                                    color=sorted_CCN[long_name],
                                    color_continuous_scale=color_scale,
                                    mapbox_style="carto-positron",
                                    width=2000,
                                    height=1200)

    # Update the tick labels
    fig_region.update_layout(coloraxis_colorbar=dict(title=long_name, tickvals=tick_vals, ticktext=tick_names, tickfont=dict(size=15, color='black')))

    fig_region.update_layout(    mapbox=dict(
            zoom=5,
            center=dict(lat=17.9, lon=-71.5)
        ),	title=f"{print_val} Distribution along Caribbean's shoreline")
    fig_region.update_traces(marker=dict(size=7))
    fig_region.update_layout(legend=dict(
        traceorder='normal',
        # title=long_name,
        title_font=dict(size=14),
        itemsizing='constant',
    
    ))
    fig_region.update_layout(
        mapbox_style="carto-positron",
        mapbox_layers=[
            {
                "below": 'traces',
                "sourcetype": "raster",
                "sourceattribution": "ESRI World Imagery",
                "source": [
                    "https://services.arcgisonline.com/arcgis/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}"
                ]
            },
            # {
            #     "below": 'traces',
            #     "sourcetype": "raster",
            #     "sourceattribution": "Google Maps",
            #     "source": [
            #         "http://mt0.google.com/vt/lyrs=s&hl=en&x={x}&y={y}&z={z}"
            #     ]
            # },
            # {
            #     "below": 'traces',
            #     "sourcetype": "raster",
            #     "sourceattribution": "United States Geological Survey",
            #     "source": [
            #         "https://basemap.nationalmap.gov/arcgis/rest/services/USGSImageryOnly/MapServer/tile/{z}/{y}/{x}"
            #     ]
            # },
            # {
            #     "below": 'traces',
            #     "sourcetype": "raster",
            #     "sourceattribution": "Bing Maps Satellite Imagery",
            #     "source": [
            #         "https://t0.tiles.virtualearth.net/tiles/a{q}.jpeg?g=685&mkt=en-us&n=z"
            #     ]
            # },
        

        ]
        )

    fig_region.update_layout(
        mapbox=dict(center=dict(lat=lat + 1, lon=lon + 4), zoom=5.3),
        title=dict(
            # text="Infant Mortality Rate along Caribbean's shoreline",
            font=dict(size=25),
            x=0.5,  # Centers the title
            xanchor='center'  # Aligns the title in the center
        )
    )


    # Show the figure
    fig_region.show()


    # Save the figure
    fig_name_shoreline = gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk') + var + "Continuous- Caribbean.png"
    pio.write_image(fig_region, os.path.join(img_directory_path, fig_name_shoreline))


In [21]:
gornitz_ESL_filled_gdf

transect_id       multi-haz additive H-E CVI  \
0       BOX_116_353_2  multi-haz additive H-E CVI 2.00   
1       BOX_116_353_3  multi-haz additive H-E CVI 1.20   
2       BOX_116_353_4  multi-haz additive H-E CVI 1.20   
3       BOX_116_353_5  multi-haz additive H-E CVI 1.20   
4       BOX_116_353_6  multi-haz additive H-E CVI 1.20   
...               ...                              ...   
37504  BOX_139_002_61  multi-haz additive H-E CVI 2.00   
37505  BOX_139_002_62  multi-haz additive H-E CVI 2.00   
37506  BOX_139_002_63  multi-haz additive H-E CVI 2.00   
37507  BOX_139_002_64  multi-haz additive H-E CVI 2.00   
37508  BOX_139_002_65  multi-haz additive H-E CVI 2.00   

       Percentage of Built Up Area_percentile - Exposure level_percentile  \
0                                                      1                    
1                                                      1                    
2                                                      1                    
3                                                      1                    
4                                                      1                    
...                                                  ...                    
37504                                                  1                    
37505                                                  1                    
37506                                                  1                    
37507                                                  1                    
37508                                                  1                    

       LECZ Area÷LECZ mean elevation_percentile - Exposure level_percentile  \
0                                                      4                      
1                                                      5                      
2                                                      5                      
3                                                      5                      
4                                                      5                      
...                                                  ...                      
37504                                                  4                      
37505                                                  4                      
37506                                                  5                      
37507                                                  5                      
37508                                                  5                      

       Neashore Slope (tanβ or m^-1)_percentile - Exposure level_percentile  \
0                                                    4.0                      
1                                                    4.0                      
2                                                    4.0                      
3                                                    4.0                      
4                                                    4.0                      
...                                                  ...                      
37504                                                3.0                      
37505                                                3.0                      
37506                                                3.0                      
37507                                                3.0                      
37508                                                3.0                      

       Population Within 1km of the coastline_percentile - Exposure level_percentile  \
0                                                      1                               
1                                                      1                               
2                                                      1                               
3                                                      1                               
4                                                 

In [22]:
gornitz_ESL_filled_gdf.to_csv(save_directory+f"/{gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk')}.csv",index=False)

Curacao Multi-Criteria Risk Level for Extreme Sea Level Hazard Using Mclaughlin and Cooper (2010)